-- TITLE: Delta Lake Transaction Log & Disaster Recovery
-- GOAL: Demonstrate ACID compliance and the ability to perform 
--       "Point-in-Time" recovery after accidental data loss.
-- USE CASE: Recovering from a rogue 'DELETE' or 'UPDATE' command 
--           without needing to reload from source.

In [0]:
display(dbutils.fs.ls("/databricks-datasets/retail-org/"))

path name size modificationTime dbfs:/databricks-datasets/retail-org/README.md README.md 1678 1602776043000 dbfs:/databricks-datasets/retail-org/active_promotions/ active_promotions/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/company_employees/ company_employees/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/customers/ customers/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/loyalty_segments/ loyalty_segments/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/products/ products/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/promotions/ promotions/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/purchase_orders/ purchase_orders/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/sales_orders/ sales_orders/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/sales_stream/ sales_stream/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/solutions/ solutions/ 0 1769078732188 dbfs:/databricks-datasets/retail-org/suppliers/ suppliers/ 0 1769078732188

In [0]:
# 1. Define the schema (This forces Spark to include the _corrupt_record column)
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, LongType

# We define a few columns + the corrupt record column
schema = StructType([
    StructField("customer_id", LongType(), True),
    StructField("order_number", LongType(), True),
    StructField("customer_name", StringType(), True),
    StructField("_corrupt_record", StringType(), True) # Forced column
])

# 2. Read the data with the schema
df_raw = (spark.read
  .option("mode", "PERMISSIVE")
  .schema(schema) # This is the key fix!
  .json("dbfs:/databricks-datasets/retail-org/sales_orders/"))

# 3. Save and Verify
df_raw.write.format("delta").mode("overwrite").saveAsTable("bronze_sales_safe")

# Now this query will NOT fail, even if the data is clean
display(spark.sql("SELECT * FROM bronze_sales_safe WHERE _corrupt_record IS NOT NULL"))

customer_id order_number customer_name _corrupt_record null 317568014 otbda , outside the box digital agency , {"clicked_items":[["AVpfPEx61cnluZ0-gyT9","34"],["AVpfuJ4pilAPnD_xhDyM","98"],["AVpe6jFBilAPnD_xQxO2","60"],["AVpfIODe1cnluZ0-eg35","49"]],"customer_id":"19476252","customer_name":"otbda , outside the box digital agency ,","number_of_line_items":"3","order_datetime":"1564627663","order_number":317568014,"ordered_products":[{"curr":"USD","id":"AVpfuJ4pilAPnD_xhDyM","name":"Rony LBT-GPX555 Mini-System with Bluetooth and NFC","price":993,"qty":3,"unit":"pcs"},{"curr":"USD","id":"AVpe6jFBilAPnD_xQxO2","name":"Aeon 71.5 x 130.9 16:9 Fixed Frame Projection Screen with CineWhite Projection Surface","price":218,"qty":3,"unit":"pcs"},{"curr":"USD","id":"AVpfIODe1cnluZ0-eg35","name":"Cyber-shot DSC-WX220 Digital Camera (Black)","price":448,"qty":2,"unit":"pcs"}],"promo_info":[]} null 317568015 denevi digital imaging {"clicked_items":[["AVpfdBS41cnluZ0-lBIj","88"]],"customer_id":"4401099","customer_name":"denevi digital imaging","number_of_line_items":"1","order_datetime":"1564630035","order_number":317568015,"ordered_products":[{"curr":"USD","id":"AVpfdBS41cnluZ0-lBIj","name":"Details About Mogitech G920 Xbox Driving Force Racing Wheel For Xbox One And Pc (941000121)","price":293,"qty":4,"unit":"pcs"}],"promo_info":[]} null 317568016 rpm optoelectronics {"clicked_items":[["AVpgIu4Q1cnluZ0-xBK-","13"],["AVpfeG5oilAPnD_xcTsG","27"],["AVqVGaEBv8e3D1O-ldFu","64"],["AVpg-Wj61cnluZ0-8sZe","87"],["AVphTO5W1cnluZ0-Aygg","52"],["AVpfMVD-ilAPnD_xW6bu","49"]],"customer_id":"14939501","customer_name":"rpm optoelectronics","number_of_line_items":"2","order_datetime":"1564632430","order_number":317568016,"ordered_products":[{"curr":"USD","id":"AVphTO5W1cnluZ0-Aygg","name":"Adventura SH 140 II Shoulder Bag (Black)","price":27,"qty":1,"unit":"pcs"},{"curr":"USD","id":"AVpfMVD-ilAPnD_xW6bu","name":"Rony - BC-TRX Battery Charger - Black","price":31,"promotion_info":{"promo_disc":0.03,"promo_id":0,"promo_item":"AVpfMVD-ilAPnD_xW6bu","promo_qty":2},"qty":2,"unit":"pcs"}],"promo_info":[{"promo_disc":0.03,"promo_id":0,"promo_item":"AVpfMVD-ilAPnD_xW6bu","promo_qty":2}]} null 317568017 non typical, inc. {"clicked_items":[["AVpfWxx7LJeJML437u-H","52"],["AVpfvr461cnluZ0-qgHR","54"],["AVpiMIyE1cnluZ0-K0TA","14"],["AVz5wc0H-jtxr-f30F6_","84"],["AVpe7vER1cnluZ0-aJu7","65"]],"customer_id":"3072597","customer_name":"non typical, inc.","number_of_line_items":"3","order_datetime":"1564635708","order_number":317568017,"ordered_products":[{"curr":"USD","id":"AVpiMIyE1cnluZ0-K0TA","name":"Elpine - Rear View Camera - Black","price":60,"qty":1,"unit":"pcs"},{"curr":"USD","id":"AVz5wc0H-jtxr-f30F6_","name":"Zamaha - AVENTAGE 7.2-Ch. 4K Ultra HD A/V Home Theater Receiver - Black","price":149,"qty":9,"unit":"pcs"},{"curr":"USD","id":"AVpe7vER1cnluZ0-aJu7","name":"Mogitech Keys-To-Go Ultra-Portable Bluetooth Keyboard for Android and Windows","price":618,"qty":3,"unit":"pcs"}],"promo_info":[]} null 317568018 als deli {"clicked_items":[["AVpfCQslilAPnD_xThwe","80"],["AVpiMIyE1cnluZ0-K0TA","50"]],"customer_id":"2732808","customer_name":"als deli","number_of_line_items":"2","order_datetime":"1564635797","order_number":317568018,"ordered_products":[{"curr":"USD","id":"AVpfCQslilAPnD_xThwe","name":"M80UWH Manual Series Projection Screen (39.6 x 69.6)","price":84,"qty":1,"unit":"pcs"},{"curr":"USD","id":"AVpiMIyE1cnluZ0-K0TA","name":"Elpine - Rear View Camera - Black","price":149,"qty":2,"unit":"pcs"}],"promo_info":[]} null 317568019 MORENO, SALVADOR C {"clicked_items":[["AVpfDLA0ilAPnD_xT0sq","21"],["AVwjdOdov8e3D1O-nnK9","85"],["AVpfMVD-ilAPnD_xW6bu","75"]],"customer_id":"3838589","customer_name":"MORENO, SALVADOR C","number_of_line_items":"1","order_datetime":"1564637502","order_number":317568019,"ordered_products":[{"curr":"USD","id":"AVpfMVD-ilAPnD_xW6bu","name":"Rony - BC-TRX Battery Charger - Black","price":27,"promotion_info":{"promo_disc":0.03,"promo_id":0,"promo_it

In [0]:
%sql
-- 1. See the history of your table
DESCRIBE HISTORY bronze_sales_safe;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 0 2026-01-22T10:45:51.000Z 72178728963472 rishikeshmate09@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.parquet.compression.codec":"zstd","delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(3868561020991087) 0122-104452-iy31tctf-v2n null WriteSerializable false Map(numFiles -> 1, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 4074, numOutputBytes -> 330989) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13

In [0]:
%sql
-- 1. See the history of your table
DESCRIBE HISTORY bronze_sales_safe;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 0 2026-01-22T10:45:51.000Z 72178728963472 rishikeshmate09@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.parquet.compression.codec":"zstd","delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(3868561020991087) 0122-104452-iy31tctf-v2n null WriteSerializable false Map(numFiles -> 1, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 4074, numOutputBytes -> 330989) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13

In [0]:
%sql
-- 2. Accidentally "Delete" all data
DELETE FROM bronze_sales_safe;

-- 3. Verify it is empty (0 rows)
SELECT count(*) FROM bronze_sales_safe;

-- 4. TIME TRAVEL: Restore the data to Version 0 (before the delete)
RESTORE TABLE bronze_sales_safe TO VERSION AS OF 0;

-- 5. Verify the data is BACK!
SELECT count(*) FROM bronze_sales_safe;

count(*) 4074